GCP GET CLI Details

In [1]:
import os
import json
from dotenv import load_dotenv
import pandas as pd
from google.oauth2 import service_account
from googleapiclient import discovery

load_dotenv()
KEY_PATH = os.getenv("GOOGLE_APPLICATION_CREDENTIALS")   # e.g. path/to/service-account.json
PROJECT  = os.getenv("GCP_PROJECT") 
print(f"Using project: {PROJECT}")
print(f"Using key: {KEY_PATH}")

Using project: premium-client-457109-p2
Using key: /home/pratyush/Downloads/gcp_cloud_tuner_2_connection.json


In [2]:
creds   = service_account.Credentials.from_service_account_file(KEY_PATH)
compute = discovery.build("compute", "v1", credentials=creds)

In [9]:
def collect_all_machine_types():
    rows = []
    request = compute.machineTypes().aggregatedList(project=PROJECT)
    while request:
        resp = request.execute()
        for zone_uri, zone_block in resp.get("items", {}).items():
            # zone_uri looks like "zones/us-central1-a"
            zone   = zone_uri.split("/")[-1]
            region = zone.rsplit("-", 1)[0]          # us-central1
            for m in zone_block.get("machineTypes", []):
                rows.append({
                    "Zone":            zone,
                    "Region":          region,
                    "MachineType":     m["name"],
                    "vCPUs":           m["guestCpus"],
                    "MemoryMiB":       m["memoryMb"],
                    "MemoryGiB":       round(m["memoryMb"]/1024, 2),
                    "Accelerators":    m.get("accelerators"),        # GPUs/FPGAs
                    "Deprecated":      m.get("deprecated"),          # if any
                    "SelfLink":        m.get("selfLink"),
                    "Description":     m.get("description"),
                })
        request = compute.machineTypes().aggregatedList_next(
            previous_request=request, previous_response=resp
        )
    return pd.DataFrame(rows)

In [10]:
df = collect_all_machine_types()
print(df.columns.tolist())
print(df.head())

['Zone', 'Region', 'MachineType', 'vCPUs', 'MemoryMiB', 'MemoryGiB', 'Accelerators']
            Zone       Region     MachineType  vCPUs  MemoryMiB  MemoryGiB  \
0  us-central1-a  us-central1   a2-highgpu-1g     12      87040       85.0   
1  us-central1-a  us-central1   a2-highgpu-2g     24     174080      170.0   
2  us-central1-a  us-central1   a2-highgpu-4g     48     348160      340.0   
3  us-central1-a  us-central1   a2-highgpu-8g     96     696320      680.0   
4  us-central1-a  us-central1  a2-megagpu-16g     96    1392640     1360.0   

                                        Accelerators  
0  [{'guestAcceleratorType': 'nvidia-tesla-a100',...  
1  [{'guestAcceleratorType': 'nvidia-tesla-a100',...  
2  [{'guestAcceleratorType': 'nvidia-tesla-a100',...  
3  [{'guestAcceleratorType': 'nvidia-tesla-a100',...  
4  [{'guestAcceleratorType': 'nvidia-tesla-a100',...  


In [11]:
print(df.to_string())

                            Zone                   Region            MachineType  vCPUs  MemoryMiB  MemoryGiB                                                                     Accelerators
0                  us-central1-a              us-central1          a2-highgpu-1g     12      87040      85.00      [{'guestAcceleratorType': 'nvidia-tesla-a100', 'guestAcceleratorCount': 1}]
1                  us-central1-a              us-central1          a2-highgpu-2g     24     174080     170.00      [{'guestAcceleratorType': 'nvidia-tesla-a100', 'guestAcceleratorCount': 2}]
2                  us-central1-a              us-central1          a2-highgpu-4g     48     348160     340.00      [{'guestAcceleratorType': 'nvidia-tesla-a100', 'guestAcceleratorCount': 4}]
3                  us-central1-a              us-central1          a2-highgpu-8g     96     696320     680.00      [{'guestAcceleratorType': 'nvidia-tesla-a100', 'guestAcceleratorCount': 8}]
4                  us-central1-a             

In [12]:
print("Number of rows:", df.shape[0])  # Total rows
print("Number of columns:", df.shape[1])  # Total columns
print(df.count())

Number of rows: 23824
Number of columns: 7
Zone            23824
Region          23824
MachineType     23824
vCPUs           23824
MemoryMiB       23824
MemoryGiB       23824
Accelerators      781
dtype: int64


In [13]:
output_path = "gcp_machine_sizes_data.csv"
df.to_csv(output_path, index=False)

print(f"Exported {len(df)} rows to {output_path}")

Exported 23824 rows to gcp_machine_sizes_data.csv
